<center><h1>WRN: Cifar10</h1></center>

## Imports

In [1]:
from __future__ import division,print_function

%matplotlib inline
%load_ext autoreload
%autoreload 2

import sys
from tqdm import tqdm_notebook as tqdm

import random
import matplotlib.pyplot as plt
import math

import numpy as np

import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
import torch.nn.init as init
from torch.autograd import Variable, grad
from torchvision import datasets, transforms
from torch.nn.parameter import Parameter
import pandas as pd
import utils.calculate_log as callog
from utils.wrn import WideResNet

from utils.detector import Detector, gram_margin_loss
import utils.attacks as attacks

import warnings
warnings.filterwarnings('ignore')

In [2]:
torch.cuda.set_device(3)

## Model definition

In [3]:
torch_model = WideResNet(depth=40, widen_factor=2, num_classes=10)

torch_model.load(path="benchmark_ckpts/cifar10_reg_training_99.pt")
torch_model.cuda()
torch_model.params = list(torch_model.parameters())
torch_model.eval()
print("Done")    

Done


## Datasets

<b>In-distribution Datasets</b>

In [4]:
batch_size = 256
# mean = np.array([[125.3/255, 123.0/255, 113.9/255]]).T

# std = np.array([[63.0/255, 62.1/255.0, 66.7/255.0]]).T
# normalize = transforms.Normalize((125.3/255, 123.0/255, 113.9/255), (63.0/255, 62.1/255.0, 66.7/255.0))

normalize = transforms.Normalize((0.5, 0.5, 0.5), (0.5, 0.5, 0.5))

transform_train = transforms.Compose([
        transforms.RandomCrop(32, padding=4),
        transforms.RandomHorizontalFlip(),
        transforms.ToTensor(),
        normalize
        
    ])
transform_test = transforms.Compose([
        transforms.CenterCrop(size=(32, 32)),
        transforms.ToTensor(),
        normalize
    ])

train_loader = torch.utils.data.DataLoader(
    datasets.CIFAR10('~/datasets/cifarpy', train=True, download=True,
                   transform=transform_train),
    batch_size=batch_size, shuffle=True)
test_loader = torch.utils.data.DataLoader(
    datasets.CIFAR10('~/datasets/cifarpy', train=False, transform=transform_test),
    batch_size=batch_size)


detector_data_transform = transforms.Compose([transforms.ToTensor(), normalize])
data_train = list(torch.utils.data.DataLoader(
        datasets.CIFAR10('~/datasets/cifarpy', 
                     train=True, 
                     transform=detector_data_transform, 
                     download=True),
        batch_size=1, shuffle=False))

data_test = list(torch.utils.data.DataLoader(
        datasets.CIFAR10('~/datasets/cifarpy', 
                     train=False, 
                     transform=detector_data_transform, 
                     download=True),
        batch_size=1, shuffle=False))

Files already downloaded and verified
Files already downloaded and verified
Files already downloaded and verified


In [5]:
def pipeline_batch(bxs):
    pil = transforms.ToPILImage()
    return torch.squeeze(torch.stack([transform_test(pil(bx)) for bx in bxs]), dim=1)

def get_batches(d, batch_size=32):
    bx = []
    by = []
    tens = transforms.ToTensor()
    for idx in range(0,len(d),batch_size):
        bx_batch = torch.squeeze(torch.stack([tens(x[0]) for x in d[idx:idx+batch_size]]),dim=1)
        bx.append(bx_batch)
        by.append(torch.Tensor([x[1] for x in d[idx:idx+batch_size]]).type(torch.LongTensor))
    
    return bx, by

def advs_p(p, bxs, bys, nrof_batches=None):
    if nrof_batches is None:
        nrof_batches = len(bxs)
        
    advs = []
    for i in tqdm(range(len(bxs))):
        if i >= nrof_batches:
            break
        
        _, feats_reg = torch_model.gram_forward((bxs[i]*2 - 1).cuda())
        advs_batch = p(torch_model, bxs[i].cuda(), bys[i].cuda(), feats_reg)

        advs.append(advs_batch)

    torch.cuda.empty_cache()
    
    return advs

def adversarial_acc(advs, bys):
    torch_model.eval()
    correct = 0
    total = 0

    for i in range(len(advs)):
        pipelined = pipeline_batch(advs[i].cpu())

        x = pipelined.cuda()
        y = bys[i].numpy()

        correct += (y==np.argmax(torch_model(x).detach().cpu().numpy(),axis=1)).sum()
        total += y.shape[0]


    print("Adversarial Test Accuracy: ", correct/total)
    
def ds_grouped(bxs, bys):
    ds = []
    for i in range(len(bxs)):
        pipelined = pipeline_batch(bxs[i].cpu())
        for j in range(len(bxs[i])):
            ds.append((pipelined[j], bys[i][j]))
    return ds

def adversarial_scores(detector, advs_batches, pbar = lambda x, total=None: x):
    auroc = []
    for batch in pbar(advs_batches):
        auroc.append(detector.compute_ood_deviations_batch(batch*2 - 1)["AUROC"])
    
    return np.mean(auroc)
    
    
def model_accuracy():
    torch_model.eval()
    correct = 0
    total = 0
    for x,y in test_loader:
        x = x.cuda()
        y = y.numpy()
        correct += (y==np.argmax(torch_model(x).detach().cpu().numpy(),axis=1)).sum()
        total += y.shape[0]
        
    return correct/total

<center><h1> Results </h1></center>

In [6]:
model_accuracy()

0.9462

In [6]:
adversary = attacks.PGD(epsilon=8./255, num_steps=10, step_size=2./255).cuda()

In [6]:
detector = Detector(torch_model, data_train, data_test, 512, pbar=None)

In [11]:
cifar10 = list(datasets.CIFAR10('~/datasets/cifarpy', train=False))

print("Calculating L_Inf")
xs, ys = get_batches(cifar10, batch_size=128)
# pinf = PGD()
# pinf = adversary
pinf = PGD_margin().cuda()
advs_inf = advs_p(pinf, xs, ys)

adversarial_acc(advs_inf, ys)

adversarial_scores(detector, advs_inf, pbar=tqdm)

Calculating L_Inf



Adversarial Test Accuracy:  0.0906


0.9460126977848102

In [8]:
cifar10 = list(datasets.CIFAR10('~/datasets/cifarpy', train=False))
xs, ys = get_batches(cifar10, batch_size=32)

In [9]:
# attacker = PGD_margin().cuda()
attacker = attacks.PGD(epsilon=8./255, num_steps=10, step_size=2./255).cuda()

data = {}

def feats_idxs(feats, idxs):
    return [f[idxs] for f in feats]

def process_batch(x, y):
    x, y = x.cuda(), y.cuda()
    
    output_reg, feats_reg = torch_model.gram_forward(x*2 - 1)
    output_reg = output_reg.cpu()
#     adv_x = attacker(torch_model, x, y, feats_reg)
    adv_x = attacker(torch_model, x, y)
#     auroc = detector.compute_ood_deviations_batch(adv_x*2 - 1)
    
    output_adv, feats_adv = torch_model.gram_forward(adv_x * 2 - 1)
    
    
    indices_adv = torch.max(output_adv.cpu(), 1)[1]
    del adv_x
    del output_adv
    del output_reg
    del x
    
    loss = []
    for i in range(10):
        idxs_adv = torch.where(i == indices_adv)[0].cpu().numpy()
        idxs_reg = torch.where(i == y)[0].cpu().numpy()
        
        batch_size = min(len(idxs_adv), len(idxs_reg))
        if batch_size == 0:
            continue
            
        idxs_adv, idxs_reg = idxs_adv[:batch_size], idxs_reg[:batch_size]
                
        loss = gram_margin_loss(feats_idxs(feats_reg, idxs_reg), feats_idxs(feats_adv, idxs_adv), 20)
        
        if i not in data:
            data[i] = []
        
        data[i].append(loss)

#     margin_loss = gram_margin_loss(feats_reg, feats_adv, 200)
    
    del y
    del indices_adv
    
#     return float(loss.mean()), float(output_adv.max(dim=1)[1].eq(y).sum())/len(x), auroc["AUROC"]
    return float(loss.mean())

In [10]:
losses = []
for i, x in tqdm(enumerate(xs), total=len(xs)):
    if i % 5 != 0:
        continue
        
    loss = process_batch(x, ys[i])
    
    print(loss)

0.0
0.0


RuntimeError: CUDA out of memory. Tried to allocate 20.00 MiB (GPU 3; 10.92 GiB total capacity; 10.28 GiB already allocated; 15.56 MiB free; 10.33 GiB reserved in total by PyTorch)

In [12]:
import gc
for obj in gc.get_objects():
    try:
        if torch.is_tensor(obj) or (hasattr(obj, 'data') and torch.is_tensor(obj.data)):
            print(type(obj), obj.size())
    except:
        pass

<class 'torch.Tensor'> torch.Size([])
<class 'torch.Tensor'> torch.Size([])
<class 'torch.Tensor'> torch.Size([])
<class 'torch.Tensor'> torch.Size([])
<class 'torch.Tensor'> torch.Size([])
<class 'torch.Tensor'> torch.Size([])
<class 'torch.Tensor'> torch.Size([])
<class 'torch.Tensor'> torch.Size([])
<class 'torch.Tensor'> torch.Size([])
<class 'torch.Tensor'> torch.Size([])
<class 'torch.nn.parameter.Parameter'> torch.Size([16, 3, 3, 3])
<class 'torch.nn.parameter.Parameter'> torch.Size([32, 32, 3, 3])
<class 'torch.nn.parameter.Parameter'> torch.Size([32])
<class 'torch.nn.parameter.Parameter'> torch.Size([32])
<class 'torch.nn.parameter.Parameter'> torch.Size([32, 32, 3, 3])
<class 'torch.nn.parameter.Parameter'> torch.Size([32])
<class 'torch.nn.parameter.Parameter'> torch.Size([32])
<class 'torch.nn.parameter.Parameter'> torch.Size([32, 32, 3, 3])
<class 'torch.nn.parameter.Parameter'> torch.Size([32])
<class 'torch.nn.parameter.Parameter'> torch.Size([32])
<class 'torch.nn.para

<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'

<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'

<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'

<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'

...

<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'

<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'

<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([1])
<class 'torch.Tensor'> torch.Size([1, 3, 32, 32])
<class 'torch.Tensor'

<class 'torch.Tensor'> torch.Size([1, 128])
<class 'torch.Tensor'> torch.Size([1, 128])
<class 'torch.Tensor'> torch.Size([1, 128])
<class 'torch.Tensor'> torch.Size([1, 128])
<class 'torch.Tensor'> torch.Size([1, 128])
<class 'torch.Tensor'> torch.Size([1, 128])
<class 'torch.Tensor'> torch.Size([1, 128])
<class 'torch.Tensor'> torch.Size([1, 16])
<class 'torch.Tensor'> torch.Size([1, 16])
<class 'torch.Tensor'> torch.Size([1, 16])
<class 'torch.Tensor'> torch.Size([1, 16])
<class 'torch.Tensor'> torch.Size([1, 32])
<class 'torch.Tensor'> torch.Size([1, 32])
<class 'torch.Tensor'> torch.Size([1, 32])
<class 'torch.Tensor'> torch.Size([1, 32])
<class 'torch.Tensor'> torch.Size([1, 32])
<class 'torch.Tensor'> torch.Size([1, 32])
<class 'torch.Tensor'> torch.Size([1, 32])
<class 'torch.Tensor'> torch.Size([1, 32])
<class 'torch.Tensor'> torch.Size([1, 32])
<class 'torch.Tensor'> torch.Size([1, 32])
<class 'torch.Tensor'> torch.Size([1, 32])
<class 'torch.Tensor'> torch.Size([1, 32])
<cla

<class 'torch.Tensor'> torch.Size([128])
<class 'torch.Tensor'> torch.Size([128, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([128])
<class 'torch.Tensor'> torch.Size([128, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([128])
<class 'torch.Tensor'> torch.Size([128, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([128])
<class 'torch.Tensor'> torch.Size([128, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([128])
<class 'torch.Tensor'> torch.Size([128, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([128])
<class 'torch.Tensor'> torch.Size([128, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([128])
<class 'torch.Tensor'> torch.Size([128, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([128])
<class 'torch.Tensor'> torch.Size([128, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([128])
<class 'torch.Tensor'> torch.Size([128, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([128])
<class 'torch.Tensor'> torch.Size([128, 3, 32, 32])
<class 'torch.Tensor'> torch.Size([128])
<class 'torch.Tensor'> torch.

In [7]:
def G_p(temp):
    temp = temp.reshape(temp.shape[0],temp.shape[1],-1)
    temp = ((torch.matmul(temp,temp.transpose(dim0=2,dim1=1)))).sum(dim=2)
    return temp.reshape(temp.shape[0],-1)

class PGD_margin(nn.Module):
    def __init__(self, epsilon=8./255, num_steps=10, step_size=2./255, grad_sign=True):
        super().__init__()
        self.epsilon = epsilon
        self.num_steps = num_steps
        self.step_size = step_size
        self.grad_sign = grad_sign

    def forward(self, model, bx, by, feats_reg):
        """
        :param model: the classifier's forward method
        :param bx: batch of images
        :param by: true labels
        :return: perturbed batch of images
        """
        adv_bx = bx.detach()
        adv_bx += torch.zeros_like(adv_bx).uniform_(-self.epsilon, self.epsilon)

        for i in range(self.num_steps):
            adv_bx.requires_grad_()
            with torch.enable_grad():
                logits, feats_adv = model.gram_forward(adv_bx * 2 - 1)
                margin_loss = gram_margin_loss(feats_reg, feats_adv, margin=20).cuda()
                
                loss = 1/2 * F.cross_entropy(logits, by, reduction='sum') + 1/2 * margin_loss
                
            grad = torch.autograd.grad(loss, adv_bx, only_inputs=True)[0]
            adv_bx = adv_bx.detach() + self.step_size * torch.sign(grad.detach())
            adv_bx = torch.min(torch.max(adv_bx, bx - self.epsilon), bx + self.epsilon).clamp(0, 1)
            
        return adv_bx
